In [1]:
import copy

In [2]:
class block:
    
    def __init__(self, block_id, x, y, z, color = None):                             
        self.block_id = block_id
        self.x = int(x)
        self.y = int(y)
        self.z = int(z)
        self.color = color
        self.top = None
        self.below = None
        self.sides = []
        self.grabbed = False
        
    def __lt__(self, other):
         return int(self.block_id[5:]) < int(other.block_id[5:])
        
    def __eq__(self, other):
        if(other == "table" or other == None):
            return False
        else:
            return self.block_id == other.block_id
        
    def __ne__(self, other):
        if(other == "table" or other == None):
            return True
        else:
            return self.block_id != other.block_id
        
    def set_top(self, block_one):
        if(self != block_one.top):
            if(self.below != None): self.below.top = None
            self.below = block_one
            block_one.top = self
    
    def remove_bottom(self):
        if(self.below != None): self.below.top = None
        self.below = None
    
    def add_side(self, block_one):
        if(self not in block_one.sides):
            self.sides.append(block_one)
            block_one.sides.append(self)
        
    def remove_sides(self):
        for s in self.sides:
            s.sides.remove(self)
        self.sides = []
        
    def __repr__(self):
        return "{" + self.block_id +", ("+str(self.x) + ", " + str(self.y) + ", " + str(self.z) + "), (" + \
        "color: " + ("None", self.color)[self.color != None] + "), (on-top-of: " + \
        ("None" if self.top == None else self.top.block_id) + "), (side-by-side: " + \
        str([x.block_id for x in self.sides]) + ")}\n"
        
    def __str__(self):
        return "{" + self.block_id +", ("+str(self.x) + ", " + str(self.y) + ", " + str(self.z) + "), (" + \
        "color: " + ("None", self.color)[self.color != None] + "), (on-top-of: " + \
        ("None" if self.top == None else self.top.block_id) + "), (side-by-side: " + \
        str([x.block_id for x in self.sides]) + ")}\n"

In [3]:
def grabbed(state):
    if(True in [x.grabbed for x in state]):
        return True
    return False

In [4]:
def find(x, y, z, state):
    return next((a for a in state if (a.x == int(x) and a.y == int(y) and a.z == int(z))), None)

In [5]:
def find2(block_id, state):
    return next((a for a in state if (a.block_id == block_id)), None)

In [6]:
def grab(block_one, state):
    if(grabbed(state)):
        print("Cannot grab! A block is already grabbed")
    elif(block_one.top != None):
        print("Cannot grab! " + block_one.block_id + " has a block on top of it")
    else:
        block_one.grabbed = True

In [7]:
def get_grabbed(state):
    for inds, s in enumerate(state):
        if(s.grabbed == True):
            return (inds, s)
    return (-1, None)

In [8]:
def release(block_one, state):
    if(block_one.grabbed == False):
        print("Cannot release! " + block_one.block_id + " is not currently grabbed")
    elif(block_one.z > 0 and (find(block_one.x, block_one.y, block_one.z - 1, state) == None)):
        print("Cannot release! There is no block underneath that spot")
    else:
        block_one.grabbed = False

In [9]:
def carry(block_one, deltax, deltay, deltaz, state):
    if(block_one.grabbed == False):
        print("Cannot carry! " + block_one.block_id + " is not currently grabbed")
    elif(find(block_one.x + deltax, block_one.y + deltay, block_one.z + deltaz, state) != None):
        print("Cannot carry " + block_one.block_id + "! There is already a block in spot " + str((block_one.x + deltax, block_one.y + deltay, block_one.z + deltaz)))
    else:
        block_one.x = block_one.x + deltax
        block_one.y = block_one.y + deltay
        block_one.z = block_one.z + deltaz
        block_one.remove_bottom()
        block_one.remove_sides()
        zdown = find(block_one.x, block_one.y, block_one.z - 1, state)
        xup = find(block_one.x + 1, block_one.y, block_one.z, state)
        xdown = find(block_one.x - 1, block_one.y, block_one.z, state)
        yup = find(block_one.x, block_one.y + 1, block_one.z, state)
        ydown = find(block_one.x, block_one.y - 1, block_one.z, state)
        if(zdown != None): block_one.set_top(zdown)
        if(xup != None): block_one.add_side(xup)
        if(xdown != None): block_one.add_side(xdown)
        if(yup != None): block_one.add_side(yup)
        if(ydown != None): block_one.add_side(ydown)
            

In [10]:
def slide(block_one, deltax, deltay, state):
    if(grabbed(state)):
        print("Cannot slide! A block is grabbed")
    elif(block_one.z != 0):
        print("Cannot slide! " + block_one.block_id + " is not at height 0")
    elif(find(block_one.x + deltax, block_one.y + deltay, block_one.z, state) != None):
        print("Cannot slide! There is already a block in spot " + str((block_one.x + deltax, block_one.y + deltay, block_one.z)))
    else:
        block_one.x = block_one.x + deltax
        block_one.y = block_one.y + deltay
        block_one.remove_sides()
        xup = find(block_one.x + 1, block_one.y, block_one.z, state)
        xdown = find(block_one.x - 1, block_one.y, block_one.z, state)
        yup = find(block_one.x, block_one.y + 1, block_one.z, state)
        ydown = find(block_one.x, block_one.y - 1, block_one.z, state)
        if(xup != None): block_one.add_side(xup)
        if(xdown != None): block_one.add_side(xdown)
        if(yup != None): block_one.add_side(yup)
        if(ydown != None): block_one.add_side(ydown)
        temp = block_one
        while(temp.top != None):
            temp = temp.top
            temp.x = temp.x + deltax
            temp.y = temp.y + deltay
            temp.remove_sides()
            xup = find(temp.x + 1, temp.y, temp.z, state)
            xdown = find(temp.x - 1, temp.y, temp.z, state)
            yup = find(temp.x, temp.y + 1, temp.z, state)
            ydown = find(temp.x, temp.y - 1, temp.z, state)
            if(xup != None): temp.add_side(xup)
            if(xdown != None): temp.add_side(xdown)
            if(yup != None): temp.add_side(yup)
            if(ydown != None): temp.add_side(ydown)
            

In [108]:
def actions_2(state):
    actions = []
    slides = [(-1,1), (0,1), (1,1), (1,0), (1,-1), (0,-1), (-1,-1), (-1,0)]
    carries = [(-1,1,0), (0,1,0), (1,1,0), (1,0,0), (1,-1,0), (0,-1,0), (-1,-1,0), (-1,0,0), (-1,1,1), (0,1,1), (1,1,1), (1,0,1), (1,-1,1), (0,-1,1), (-1,-1,1), (-1,0,1), (0,0,1), (-1,1,-1), (0,1,-1), (1,1,-1), (1,0,-1), (1,-1,-1), (0,-1,-1), (-1,-1,-1), (-1,0,-1), (0,0,-1)]
    grabs = []
    if not(grabbed(state)):
        for inda, a in enumerate(state):
            if(a.z == 0):
                for s in slides:
                    if(9 >= a.x + s[0] >= 0 and 9 >= a.y + s[1] >= 0 and find(a.x + s[0], a.y + s[1], 0, state) == None):
                        actions.append(("slide", (inda, a.block_id), s))
        for inda, a in enumerate(state):
            if(a.top == None):
                grabs.append(("grab", (inda, a.block_id)))
    if(grabbed(state)):
        grabbed_block = get_grabbed(state)
        for c in carries:
                if(grabbed_block[1].z + c[2] >= 0 and 9 >= grabbed_block[1].x + c[0] >= 0 and 9 >= grabbed_block[1].y + c[1] >= 0 and find(grabbed_block[1].x + c[0], grabbed_block[1].y + c[1], grabbed_block[1].z + c[2], state) == None):
                    actions.append(("carry", (grabbed_block[0], grabbed_block[1].block_id), c))
        if(grabbed_block[1].z == 0 or grabbed_block[1].below != None):
            grabs.append(("release", (grabbed_block[0], grabbed_block[1].block_id)))
    return grabs + actions

In [12]:
def take_action_2(action, state):
    newState = copy.deepcopy(state)
    if(action[0] == "slide"):
        slide(newState[action[1][0]], action[2][0], action[2][1], newState)
    elif(action[0] == "release"):
        release(newState[action[1][0]], newState)
    elif(action[0] == "carry"):
        carry(newState[action[1][0]], action[2][0], action[2][1], action[2][2], newState)
    elif(action[0] == "grab"):
        grab(newState[action[1][0]], newState)
 
    return newState

In [13]:
def read_startState(file_name):
    f = list(open(file_name, "r"))
    state = []
    for x in f:
        if(len(x.split()) == 6):
            ary = x.replace("(", "").replace(")", "").split()
            if(ary[0] == "has"):
                new_block = block(ary[1], ary[3], ary[4], ary[5])
                state.append(new_block)
    for s in state:
        zup = find(s.x, s.y, s.z + 1, state)
        zdown = find(s.x, s.y, s.z - 1, state)
        xup = find(s.x + 1, s.y, s.z, state)
        xdown = find(s.x - 1, s.y, s.z, state)
        yup = find(s.x, s.y + 1, s.z, state)
        ydown = find(s.x, s.y - 1, s.z, state)
        if(zup != None): zup.set_top(s)
        if(zdown != None): s.set_top(zdown)
        if(xup != None): s.add_side(xup)
        if(xdown != None): s.add_side(xdown)
        if(yup != None): s.add_side(yup)
        if(ydown != None): s.add_side(ydown)
    for z in f:
        if(len(z.split()) == 4):
            ary = z.replace("(", "").replace(")", "").split()
            if(ary[0] == "has"):
                block_one = next((a for a in state if (a.block_id == ary[1])), None)
                block_one.color = ary[3]
                
    return sorted(state)

In [14]:
def read_goalState(file_name):
    return sorted(list(open(file_name, "r")))

In [ ]:

# print(state)
# check(state, goalState)

In [60]:
def check(state, goalState):
    wildcards = {}
    for x in goalState:
        if(len(x.split()) == 4 or len(x.split()) == 6):
            ary = x.replace("(", "").replace(")", "").split()
            state_block_ids = [y.block_id for y in state]
            
            if(ary[0] == "has" and ary[1][:8] != "wildcard"):
                if(ary[1] not in state_block_ids):
                    print("Block in goal isn't in state")
                    return False
                if(len(x.split()) == 6):
                    temp = find(ary[3], ary[4], ary[5], state)
                    if(temp == None or temp.block_id != ary[1]):
                        return False
            if(ary[0] == "is" and ary[2][:8] != "wildcard" and ary[1][:8] != "wildcard"):
                if((ary[2] not in state_block_ids) or (ary[1] not in state_block_ids)):
                        print("Block in goal isn't in state")
                        return False
                if(ary[3] == "on-top-of"):
                        for z in state:
                            if(z.block_id == ary[2] and (z.top.block_id if z.top != None else None) != ary[1]):
                                return False

                if(ary[3] == "side-by-side"):
                    for z in state:
                        if(z.block_id == ary[2] and (ary[1] not in [w.block_id for w in z.sides])):
                            return False
                        
       
            if(ary[0] == "has" and ary[1][:8] == "wildcard"):
                if(len(x.split()) == 4):
                    no_color = True
                    for z in state:
                        if(z.color == ary[3]):
                            no_color = False
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [z]
                            else:
                                wildcards[ary[1]].append(z)
                    if(no_color):
                        print("There is no block that is color " + ary[3])
                        return False
                if(len(x.split()) == 6):
                    temp = find(ary[3], ary[4], ary[5], state)
                    if(temp == None):
                        return False
                    elif(wildcards.get(ary[1], 0) == 0):
                        wildcards[ary[1]] = [temp]
                    else:
                        remove = []
                        for y in wildcards[ary[1]]:
                            if(y != temp):
                                remove = remove + [y]
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
            if(ary[0] == "is" and (ary[2][:8] == "wildcard" or ary[1][:8] == "wildcard")):
                if(ary[3] == "on-top-of" and ary[2][:8] != "wildcard"):
                    block_two = next((a for a in state if a.block_id == ary[2]), None)
                    if(block_two.top == None):
                        return False
                    elif(wildcards.get(ary[1], 0) == 0):
                        wildcards[ary[1]] = [block_two.top]
                    else:
                        remove = []
                        for w in wildcards[ary[1]]:
                            if(w.below != block_two):
                                remove = remove + [w]
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                elif(ary[3] == "on-top-of" and ary[1][:8] != "wildcard"):
                    print("Wildcard not initialized2")
                    print(wildcards)
                    block_one = next((a for a in state if a.block_id == ary[1]), None)
                    if(block_one.below == None):
                        return False
                    elif(wildcards.get(ary[2], 0) == 0):
                        wildcards[ary[2]] = [block_one.below]
                    else:
                        remove = []
                        for w in wildcards[ary[2]]:
                            if(w.top != block_one):
                                remove = remove + [w]
                        for r in remove:
                            wildcards[ary[2]].remove(r)
                        if(wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0):
                            print(wildcards)
                            print("BINGO")
                            return False
                elif(ary[3] == "on-top-of"):
                    if(wildcards.get(ary[1], 0) == 0 and wildcards.get(ary[2], 0) == 0):
                        for v in state:
                            if(v.top != None):
                                if(wildcards.get(ary[1], 0) == 0): 
                                    wildcards[ary[1]] = [v.top]
                                else:
                                    wildcards[ary[1]].append(v.top)
                                if(wildcards.get(ary[2], 0) == 0): 
                                    wildcards[ary[2]] = [v]
                                else:
                                    wildcards[ary[2]].append(v)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    elif(wildcards.get(ary[2], 0) == 0):
                        remove = []
                        for w in wildcards[ary[1]]:
                            if(w.below == None):
                                remove = remove + [w]
                            else:
                                if(wildcards.get(ary[2], 0) == 0):
                                    wildcards[ary[2]] = [w.below]
                                else:
                                    wildcards[ary[2]].append(w.below)
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    elif(wildcards.get(ary[1], 0) == 0):
                        remove = []
                        for w in wildcards[ary[2]]:
                            if(w.top == None):
                                remove = remove + [w]
                            else:
                                if(wildcards.get(ary[1], 0) == 0):
                                    wildcards[ary[1]] = [w.top]
                                else:
                                    wildcards[ary[1]].append(w.top)
                        for r in remove:
                            wildcards[ary[2]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False  
                    else:
                        remove = []
                        for m in wildcards[ary[1]]:
                            not_related_1 = True
                            for n in wildcards[ary[2]]:
                                if(m.below == n):
                                    not_related_1 = False
                            if(not_related_1):
                                remove = remove + [m]
                        for r in  remove:
                            wildcards[ary[1]].remove(r)   
                            
                        remove = []
                        for m in wildcards[ary[2]]:
                            not_related_2 = True
                            for n in wildcards[ary[1]]:
                                if(m.top == n):
                                    not_related_2 = False
                            if(not_related_2):
                                remove = remove + [m]
                        for r in remove:
                            wildcards[ary[2]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False



                elif(ary[3] == "side-by-side" and ary[2][:8] != "wildcard"):
                    block_two = next((a for a in state if a.block_id == ary[2]), None)
                    if(len(block_two.sides) == 0):
                        return False
                    elif(wildcards.get(ary[1], 0) == 0):
                        for j in block_two.sides:
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [j]
                            else:
                                wildcards[ary[1]].append(j)
                        if(wildcards.get(ary[1], 0) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    else:
                        remove = []
                        for w in wildcards[ary[1]]:
                            if(w not in block_two.sides):
                                remove = remove + [w]
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                elif(ary[3] == "side-by-side" and ary[1][:8] != "wildcard"):
                    block_one = next((a for a in state if a.block_id == ary[1]), None)
                    if(len(block_one.sides) == 0):
                        return False
                    elif(wildcards.get(ary[2], 0) == 0):
                        for j in block_one.sides:
                            if(wildcards.get(ary[2], 0) == 0):
                                wildcards[ary[2]] = [j]
                            else:
                                wildcards[ary[2]].append(j)
                        if(wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0):
                                return False
                    else:
                        remove = []
                        for w in wildcards[ary[2]]:
                            if(w not in block_one.sides):
                                remove = remove + [w]
                        for r in remove:
                             wildcards[ary[2]].remove(2)
                        if(wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0):
                            return False
                elif(ary[3] == "side-by-side"):
                    if(wildcards.get(ary[1], 0) == 0 and wildcards.get(ary[2], 0) == 0):
                        for v in state:
                            if(len(v.sides) > 0):
                                if(wildcards.get(ary[1], 0) == 0): 
                                    wildcards[ary[1]] = [v]
                                else:
                                    wildcards[ary[1]].append(v)
                                for k in v.sides:
                                    if(wildcards.get(ary[2], 0) == 0): 
                                        wildcards[ary[2]] = [k]
                                    else:
                                        wildcards[ary[2]].append(k)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    elif(wildcards.get(ary[2], 0) == 0):
                        remove = []
                        for w in wildcards[ary[1]]:
                            if(len(w.sides) == 0):
                                remove = remove + [w] 
                            else:
                                for p in w.sides:
                                    if(wildcards.get(ary[2], 0) == 0):
                                        wildcards[ary[2]] = [p]
                                    else:
                                        wildcards[ary[2]].append(p)
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    elif(wildcards.get(ary[1], 0) == 0):
                        remove = []
                        for w in wildcards[ary[2]]:
                            if(len(w.sides) == 0):
                                remove = remove + [w] 
                            else:
                                for p in w.sides:
                                    if(wildcards.get(ary[1], 0) == 0):
                                        wildcards[ary[1]] = [p]
                                    else:
                                        wildcards[ary[1]].append(p)
                        for r in remove:
                            wildcards[ary[2]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
                    else:
                        remove = []
                        for m in wildcards[ary[1]]:
                            not_related_1 = True
                            for n in wildcards[ary[2]]:
                                if(n in m.sides):
                                    not_related_1 = False
                            if(not_related_1):
                                remove = remove + [m]
                        for r in remove:
                            wildcards[ary[1]].remove(r)
                        remove = []
                        for m in wildcards[ary[2]]:
                            not_related_2 = True
                            for n in wildcards[ary[1]]:
                                if(n in m.sides):
                                    not_related_2 = False
                            if(not_related_2):
                                remove = remove + [m]
                        for r in remove:
                            wildcards[ary[2]].remove(r)
                        if(wildcards.get(ary[1], 0) == 0 or wildcards.get(ary[2], 0) == 0 or len(wildcards[ary[2]]) == 0 or len(wildcards[ary[1]]) == 0):
                            return False
    return True

In [16]:
class Node:
    def __init__(self, state, action, h=0, g=0 ,f=0):
        self.state = state
        self.action = action
        self.h = h
        self.g = g
        self.f = f
    def __repr__(self):
        return "Node(" + repr(self.state) + ", action=" + repr(self.action) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"
    def __str__(self):
        return "Node(" + repr(self.state) + ", action=" + repr(self.action) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"

In [17]:
class Node2:
    def __init__(self, state, action, moves, h=0, g=0 ,f=0):
        self.state = state
        self.action = action
        self.moves = moves
        self.h = h
        self.g = g
        self.f = f
    def __repr__(self):
        return "Node(" + repr(self.state) + ", action=" + repr(self.action) + ", moves" + repr(self.moves) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"
    def __str__(self):
        return "Node(" + repr(self.state) + ", action=" + repr(self.action) + ", moves" + repr(self.moves) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"

In [110]:
def aStarLow(parentNode, goalState, actionsF, take_actionF, hF, fmax):
    if(check(parentNode.state, goalState)):
        return([parentNode.action], parentNode.g, parentNode.state)
    actions = actionsF(parentNode.state)
    if not actions:
        return("no more moves", float("inf"))
    children = []
    for action in actions:
        childState = take_actionF(action, parentNode.state)
        h = hF(childState, goalState)
        g = parentNode.g + 1
        f = h+g
        childNode = Node(state=childState, action = action, h=h, g=g, f=f)
        children.append(childNode)
    while True:
        minChild = min(children, key = lambda x: x.f)
        print("child")
        print(minChild.state)
        print("goal")
        print(goalState)
        print("heuristic")
        print(h_5(minChild.state, goalState))
        print("childaction")
        print(minChild.action)
        print("allactions")
        print(actions)
        print("goalState")
        print(goalState)
        if minChild.f > fmax:
            return ("max steps exceded", minChild.f,  parentNode.state)
        alternativef = minChild.f if len(children) > 1 else float('inf')
        result, minChild.f, parentState= aStarLow(minChild, goalState, actionsF, take_actionF, hF, min(fmax,alternativef))
        if result is not "no more moves" and result is not "max steps exceded":         
            result.insert(0, parentNode.action) 
            return (result, minChild.f, parentState) 
        
def aStarSearchLow(startState, goalState, actionsF, take_actionF, hF, fmax):
    answer = aStarLow(Node(state=startState, action=None, f=0, g=0, h=0), goalState, actionsF, take_actionF, hF, fmax)
#     if((answer[0] ==  "max steps exceded") or (answer[0] == "no more moves")):
#         print(answer)
#     else:
#         for a in answer[0][1::]:
#             print("(" + str(a[0]) + ", " + str(a[1][1]) + ("" if (len(a) == 2) else (", " + str(a[2]))) + ")")
#     print(answer[1])
    return answer

In [19]:
def h_5(startState, goalState):
    cost = 0
    wildcards = {}
    g = get_grabbed(startState)
    print("Start")
    for x in goalState:
        if(len(x.split()) == 4 or len(x.split()) == 6):
            ary = x.replace("(", "").replace(")", "").split()
            if(ary[0] == "has" and ary[1][:8] == "wildcard"):
                if(len(x.split()) == 4):
                    for z in startState:
                        if(z.color == ary[3]):
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [z]
                            else:
                                wildcards[ary[1]].append(z)
                if(len(x.split()) == 6):
                    if(wildcards.get(ary[1], 0) == 0):
                        for z in startState:
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [z]
                            else:
                                wildcards[ary[1]].append(z)
                
            if(ary[0] == "has" and ary[1][:8] != "wildcard" and len(x.split()) == 6):
                temp = copy.deepcopy(find2(ary[1], startState))
                blocker = find(ary[3], ary[4], ary[5], startState)
                dif = max([abs(temp.x - int(ary[3])), abs(temp.y - int(ary[4])), abs(temp.z - int(ary[5]))])
                cost = cost + dif
                if(temp.z  != int(ary[5]) and get_grabbed(startState)[1] != temp and blocker != None and blocker != temp):
                    cost = cost + 1
                blocker = find(ary[3], ary[4], ary[5], startState)
                if(blocker != None and blocker != temp):
                    cost = cost + 1
                if(temp.z  != int(ary[5])):
                    while(temp.top != None):
                        temp = temp.top
                        cost = cost + 1
                        if(temp != g[1]):
                            cost = cost + 1
            if(ary[0] == "has" and ary[1][:8] == "wildcard" and len(x.split()) == 6):
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[1], 0) == 0):
                            wildcards[ary[1]] = [m]
                        else:
                            wildcards[ary[1]].append(m)
                if(wildcards.get(ary[1], 0) != 0):
                    min_card = (None, 1000)
                    for w in wildcards[ary[1]]:
                        dif = max([abs(w.x - int(ary[3])), abs(w.y - int(ary[4])), abs(w.z - int(ary[5]))])
                        if(w.z != int(ary[5])):
                            temp = copy.deepcopy(w)
                            while(temp.top != None):
                                temp = temp.top
                                dif = dif + 1
                                if(temp != g[1]):
                                    dif = dif + 1
                        if(min_card[1] > dif):
                            min_card = (w, dif)
                    cost = cost + min_card[1]
                blocker = find(ary[3], ary[4], ary[5], startState)
                if(min_card[0].z  != int(ary[5]) and get_grabbed(startState)[1] != min_card[0] and blocker != None and blocker != min_card[0]):
                    cost = cost + 1
                if(blocker != None and blocker != min_card[0]):
                    cost = cost + 1
                                
            if(ary[0] == "is" and ary[1][:8] != "wildcard" and ary[2][:8] != "wildcard"):
                block_one = copy.deepcopy(find2(ary[1], startState))
                block_two = copy.deepcopy(find2(ary[2], startState))
                block_a = copy.deepcopy(find2(ary[1], startState))
                block_b = copy.deepcopy(find2(ary[2], startState))
                if(ary[3] == "on-top-of"):
                    dif = max([abs(block_one.x - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - 1 - block_two.z)])
                    if(block_two.top != block_one):
                        while(block_one.top != None):
                            block_one = block_one.top
                            dif = dif + 1
                            if(block_one != g[1]):
                                dif = dif + 1
                        while(block_two.top != None):
                            block_two = block_two.top
                            dif = dif + 1
                            if(block_two != g[1]):
                                dif = dif + 1
                    blocker = block_two.top
                    if(blocker != block_one and get_grabbed(startState)[1] != block_one and blocker != None):
                        dif = dif + 1
                            
                else:
                    dif1 = max([abs(block_one.x + 1 - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - block_two.z)])
                    dif2 = max([abs(block_one.x - 1 - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - block_two.z)])
                    dif3 = max([abs(block_one.x - block_two.x), abs(block_one.y + 1 - block_two.y), abs(block_one.z - block_two.z)])
                    dif4 = max([abs(block_one.x - block_two.x), abs(block_one.y - 1 - block_two.y), abs(block_one.z - block_two.z)])
                    dif = min([dif1, dif2, dif3, dif4])
                    if(block_one.z != block_two.z):
                        while(block_one.top != None and block_two.top != None):
                            block_one = block_one.top
                            block_two = block_two.top
                            dif = dif + 1
                            if(block_one != g[1] or block_two != g[1]):
                                dif = dif + 1
                    if(block_a.z != block_b.z and (g[1] != block_a or g[1] != block_b )):
                        dif = dif + 2
                cost = cost + dif                              
            if(ary[0] == "is" and ary[1][:8] == "wildcard" and ary[2][:8] != "wildcard"):
                block_two = find2(ary[2], startState)
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(m != block_two):
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [m]
                            else:
                                wildcards[ary[1]].append(m)
                min_card = (None, 1000)
                for w in wildcards[ary[1]]:
                    if(ary[3] == "on-top-of"):
                        dif = max([abs(w.x - block_two.x), abs(w.y - block_two.y), abs(w.z - 1 - block_two.z)])
                        if(block_two.top != w):
                            temp_1 = copy.deepcopy(w)
                            temp_2 = copy.deepcopy(block_two)
                            while(temp_1.top != None):
                                temp_1 = temp_1.top
                                dif = dif + 1
                            while(temp_2.top != None):
                                temp_2 = temp_2.top
                                dif = dif + 1
                            blocker = block_two.top
                            if(blocker != w and get_grabbed(startState)[1] != w and blocker != None):
                                dif = dif + 1
                    else:
                        dif1 = max([abs(w.x + 1 - block_two.x), abs(w.y - block_two.y), abs(w.z - block_two.z)])
                        dif2 = max([abs(w.x - 1 - block_two.x), abs(w.y - block_two.y), abs(w.z - block_two.z)])
                        dif3 = max([abs(w.x - block_two.x), abs(w.y + 1 - block_two.y), abs(w.z - block_two.z)])
                        dif4 = max([abs(w.x - block_two.x), abs(w.y - 1 - block_two.y), abs(w.z - block_two.z)])
                        dif = min([dif1, dif2, dif3, dif4])
                        if(w.z != block_two.z):
                            temp_1 = copy.deepcopy(w)
                            temp_2 = copy.deepcopy(block_two)
                            while(temp_1.top != None and temp_2.top != None):
                                temp_1 = temp_1.top
                                temp_2 = temp_2.top
                                dif = dif + 1
                                if(temp_2 != g[1] or temp_1 != g[1]):
                                    dif = dif + 1
                    if(min_card[1] > dif):
                        min_card = (w, dif)

                cost = cost + min_card[1]                            
            if(ary[0] == "is" and ary[1][:8] != "wildcard" and ary[2][:8] == "wildcard"):
                block_one = find2(ary[1], startState)
                if(wildcards.get(ary[2], 0) == 0):
                    for m in startState:
                        if(m != block_one):
                            if(wildcards.get(ary[2], 0) == 0):
                                wildcards[ary[2]] = [m]
                            else:
                                wildcards[ary[2]].append(m)
                min_card = (None, 1000)
                for w in wildcards[ary[2]]:
                    if(w != block_one):
                        if(ary[3] == "on-top-of"):
                            dif = max([abs(block_one.x - w.x), abs(block_one.y - w.y), abs(block_one.z - 1 - w.z)])
                            if(block_one.below != w):
                                temp_1 = copy.deepcopy(block_one)
                                temp_2 = copy.deepcopy(w)
                                while(temp_1.top != None):
                                    temp_1 = temp_1.top
                                    dif = dif + 1
                                    if(temp_1 != g[1]):
                                        dif = dif + 1
                                while(temp_2.top != None):
                                    temp_2 = temp_2.top
                                    dif = dif + 1
                                    if(temp_2 != g[1]):
                                        dif = dif + 1
                                blocker = w.top
                                if(blocker != block_one and get_grabbed(startState)[1] != block_one and blocker != None):
                                    dif = dif + 1
                        else:
                            dif1 = max([abs(block_one.x + 1 - w.x), abs(block_one.y - w.y), abs(block_one.z - w.z)])
                            dif2 = max([abs(block_one.x - 1 - w.x), abs(block_one.y - w.y), abs(block_one.z - w.z)])
                            dif3 = max([abs(block_one.x - w.x), abs(block_one.y + 1 - w.y), abs(block_one.z - w.z)])
                            dif4 = max([abs(block_one.x - w.x), abs(block_one.y - 1 - w.y), abs(block_one.z - w.z)])
                            dif = min([dif1, dif2, dif3, dif4])
                            if(w.z != block_one.z):
                                temp_1 = copy.deepcopy(w)
                                temp_2 = copy.deepcopy(block_one)
                                while(temp_1.top != None and temp_2.top != None):
                                    temp_1 = temp_1.top
                                    temp_2 = temp_2.top
                                    dif = dif + 1
                                    if(temp_2 != g[1] or temp_1 != g[1]):
                                        dif = dif + 1
                        if(min_card[1] > dif):
                            min_card = (w, dif)
                cost = cost + min_card[1]
                            
            if(ary[0] == "is" and ary[1][:8] == "wildcard" and ary[2][:8] == "wildcard"):
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[1], 0) == 0):
                            wildcards[ary[1]] = [m]
                        else:
                            wildcards[ary[1]].append(m)
                if(wildcards.get(ary[2], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[2], 0) == 0):
                            wildcards[ary[2]] = [m]
                        else:
                            wildcards[ary[2]].append(m)
                min_card = (None, None, 1000)
                for w in wildcards[ary[1]]:
                    for v in wildcards[ary[2]]:
                        if(v != w):
                            if(ary[3] == "on-top-of"):
                                dif = max([abs(w.x - v.x), abs(w.y - v.y), abs(w.z - 1 - v.z)])
                                if(v.top != w):
                                    temp_1 = copy.deepcopy(w)
                                    temp_2 = copy.deepcopy(v)
                                    while(temp_1.top != None):
                                        temp_1 = temp_1.top
                                        dif = dif + 1
                                        if(temp_1 != g[1]):
                                            dif = dif + 1
                                    while(temp_2.top != None):
                                        temp_2 = temp_2.top
                                        dif = dif + 1
                                        if(temp_2 != g[1]):
                                            dif = dif + 1
                                blocker = v.top
                                if(blocker != w and g[1] != w and blocker != None):
                                    dif = dif + 1
                            else:
                                dif1 = max([abs(w.x + 1 - v.x), abs(w.y - v.y), abs(w.z - v.z)])
                                dif2 = max([abs(w.x - 1 - v.x), abs(w.y - v.y), abs(w.z - v.z)])
                                dif3 = max([abs(w.x - v.x), abs(w.y + 1 - v.y), abs(w.z - v.z)])
                                dif4 = max([abs(w.x - v.x), abs(w.y - 1 - v.y), abs(w.z - v.z)])
                                dif = min([dif1, dif2, dif3, dif4])
                                if(w.z != v.z):
                                    temp_1 = copy.deepcopy(w)
                                    temp_2 = copy.deepcopy(v)
                                    while(temp_1.top != None and temp_2.top != None):
                                        temp_1 = temp_1.top
                                        temp_2 = temp_2.top
                                        dif = dif + 1
                                        if(temp_2 != g[1] or temp_1 != g[1]):
                                            dif = dif + 1
                            if(min_card[2] > dif):
                                min_card = (w, v, dif)
                
                cost = cost + min_card[2]
    print("FINISH")
    return cost

In [80]:
def actions_H(startState, goalState):
    cost = 0
    colors = []
    actions = []
    dont = []
    sides = []
    wildcards = {}
    above = []
    blocks = []
    top1 = []
    bottom1 = []
    sides1 = []
    g = get_grabbed(startState)
    for x in goalState:
        if(len(x.split()) == 4 or len(x.split()) == 6):
            ary = x.replace("(", "").replace(")", "").split()
            if(ary[0] == "has" and ary[1][:8] == "wildcard"):
                if(len(x.split()) == 4):
                    colors.append(x)
                    for z in startState:
                        if(z.color == ary[3]):
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [z]
                            else:
                                wildcards[ary[1]].append(z)
                                
                    
    for x in goalState:
        action = []
        cost = 0
        if(len(x.split()) == 4 or len(x.split()) == 6):
            ary = x.replace("(", "").replace(")", "").split()
            if(ary[0] == "has" and ary[1][:8] != "wildcard" and len(x.split()) == 6):
                temp_1 = find2(ary[1], startState)
                temp_2 = find(int(ary[3]), int(ary[4]), int(ary[5]), startState) 
                if(temp_1 != temp_2 and temp_1.z != int(ary[5])):
                    if(temp_1.z != int(ary[5]) and temp_1.top != None):
                        actions.append("move " + temp_1.block_id + " remove-top")
                    if(temp_2 != None):
                        actions.append("move " + temp_2.block_id + " remove")
# done
            if(ary[0] == "has" and ary[1][:8] == "wildcard" and len(x.split()) == 6):
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[1], 0) == 0):
                            wildcards[ary[1]] = [m]
                        else:
                            wildcards[ary[1]].append(m)
                if(wildcards.get(ary[1], 0) != 0):
                    min_card = (None, 1000)
                    for w in wildcards[ary[1]]:
                        dif = max([abs(w.x - int(ary[3])), abs(w.y - int(ary[4])), abs(w.z - int(ary[5]))])
                        if(w.z != int(ary[5])):
                            temp = copy.deepcopy(w)
                            while(temp.top != None):
                                temp = temp.top
                                dif = dif + 1
                                if(temp != g[1]):
                                    dif = dif + 1
                        if(min_card[1] > dif):
                            min_card = (w, dif)
                    cost = cost + min_card[1]
                blocker = find(ary[3], ary[4], ary[5], startState)
                if(min_card[0].z  != int(ary[5]) and get_grabbed(startState)[1] != min_card[0] and blocker != None and blocker != min_card[0]):
                    cost = cost + 1
                if(blocker != None and blocker != min_card[0]):
                    cost = cost + 1
                                
            if(ary[0] == "is" and ary[1][:8] != "wildcard" and ary[2][:8] != "wildcard"):
                block_one = find2(ary[1], startState)
                block_two = find2(ary[2], startState)
                if(ary[3] == "on-top-of"):
                    dif = max([abs(block_one.x - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - 1 - block_two.z)])
                    if(block_two.top != block_one):
                        while(block_one.top != None):
                            block_one = block_one.top
                            dif = dif + 1
                            if(block_one != g[1]):
                                dif = dif + 1
                        while(block_two.top != None):
                            block_two = block_two.top
                            dif = dif + 1
                            if(block_two != g[1]):
                                dif = dif + 1
                    blocker = block_two.top
                    if(blocker != block_one and get_grabbed(startState)[1] != block_one and blocker != None):
                        dif = dif + 1
                            
                else:
                    dif1 = max([abs(block_one.x + 1 - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - block_two.z)])
                    dif2 = max([abs(block_one.x - 1 - block_two.x), abs(block_one.y - block_two.y), abs(block_one.z - block_two.z)])
                    dif3 = max([abs(block_one.x - block_two.x), abs(block_one.y + 1 - block_two.y), abs(block_one.z - block_two.z)])
                    dif4 = max([abs(block_one.x - block_two.x), abs(block_one.y - 1 - block_two.y), abs(block_one.z - block_two.z)])
                    dif = min([dif1, dif2, dif3, dif4])
                    if(block_one.z != block_two.z):
                        while(block_one.top != None and block_two.top != None):
                            block_one = block_one.top
                            block_two = block_two.top
                            dif = dif + 1
                            if(block_one != g[1] or block_two != g[1]):
                                dif = dif + 1
                cost = cost + dif                              
            if(ary[0] == "is" and ary[1][:8] == "wildcard" and ary[2][:8] != "wildcard"):
                block_two = find2(ary[2], startState)
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(m != block_two):
                            if(wildcards.get(ary[1], 0) == 0):
                                wildcards[ary[1]] = [m]
                            else:
                                wildcards[ary[1]].append(m)
                min_card = (None, 1000)
                for w in wildcards[ary[1]]:
                    if(ary[3] == "on-top-of"):
                        dif = max([abs(w.x - block_two.x), abs(w.y - block_two.y), abs(w.z - 1 - block_two.z)])
                        if(block_two.top != w):
                            temp_1 = copy.deepcopy(w)
                            temp_2 = copy.deepcopy(block_two)
                            while(temp_1.top != None):
                                temp_1 = temp_1.top
                                dif = dif + 1
                            while(temp_2.top != None):
                                temp_2 = temp_2.top
                                dif = dif + 1
                            blocker = block_two.top
                            if(blocker != w and get_grabbed(startState)[1] != w and blocker != None):
                                dif = dif + 1
                    else:
                        dif1 = max([abs(w.x + 1 - block_two.x), abs(w.y - block_two.y), abs(w.z - block_two.z)])
                        dif2 = max([abs(w.x - 1 - block_two.x), abs(w.y - block_two.y), abs(w.z - block_two.z)])
                        dif3 = max([abs(w.x - block_two.x), abs(w.y + 1 - block_two.y), abs(w.z - block_two.z)])
                        dif4 = max([abs(w.x - block_two.x), abs(w.y - 1 - block_two.y), abs(w.z - block_two.z)])
                        dif = min([dif1, dif2, dif3, dif4])
                        if(w.z != block_two.z):
                            temp_1 = copy.deepcopy(w)
                            temp_2 = copy.deepcopy(block_two)
                            while(temp_1.top != None and temp_2.top != None):
                                temp_1 = temp_1.top
                                temp_2 = temp_2.top
                                dif = dif + 1
                                if(temp_2 != g[1] or temp_1 != g[1]):
                                    dif = dif + 1
                    if(min_card[1] > dif):
                        min_card = (w, dif)

                cost = cost + min_card[1]                            
            if(ary[0] == "is" and ary[1][:8] != "wildcard" and ary[2][:8] == "wildcard"):
                block_one = find2(ary[1], startState)
                if(wildcards.get(ary[2], 0) == 0):
                    for m in startState:
                        if(m != block_one):
                            if(wildcards.get(ary[2], 0) == 0):
                                wildcards[ary[2]] = [m]
                            else:
                                wildcards[ary[2]].append(m)
                min_card = (None, 1000)
                for w in wildcards[ary[2]]:
                    if(w != block_one):
                        if(ary[3] == "on-top-of"):
                            dif = max([abs(block_one.x - w.x), abs(block_one.y - w.y), abs(block_one.z - 1 - w.z)])
                            if(block_one.below != w):
                                temp_1 = copy.deepcopy(block_one)
                                temp_2 = copy.deepcopy(w)
                                while(temp_1.top != None):
                                    temp_1 = temp_1.top
                                    dif = dif + 1
                                    if(temp_1 != g[1]):
                                        dif = dif + 1
                                while(temp_2.top != None):
                                    temp_2 = temp_2.top
                                    dif = dif + 1
                                    if(temp_2 != g[1]):
                                        dif = dif + 1
                                blocker = w.top
                                if(blocker != block_one and get_grabbed(startState)[1] != block_one and blocker != None):
                                    dif = dif + 1
                        else:
                            dif1 = max([abs(block_one.x + 1 - w.x), abs(block_one.y - w.y), abs(block_one.z - w.z)])
                            dif2 = max([abs(block_one.x - 1 - w.x), abs(block_one.y - w.y), abs(block_one.z - w.z)])
                            dif3 = max([abs(block_one.x - w.x), abs(block_one.y + 1 - w.y), abs(block_one.z - w.z)])
                            dif4 = max([abs(block_one.x - w.x), abs(block_one.y - 1 - w.y), abs(block_one.z - w.z)])
                            dif = min([dif1, dif2, dif3, dif4])
                            if(w.z != block_one.z):
                                temp_1 = copy.deepcopy(w)
                                temp_2 = copy.deepcopy(block_one)
                                while(temp_1.top != None and temp_2.top != None):
                                    temp_1 = temp_1.top
                                    temp_2 = temp_2.top
                                    dif = dif + 1
                                    if(temp_2 != g[1] or temp_1 != g[1]):
                                        dif = dif + 1
                        if(min_card[1] > dif):
                            min_card = (w, dif)
                cost = cost + min_card[1]
                            
            if(ary[0] == "is" and ary[1][:8] == "wildcard" and ary[2][:8] == "wildcard"):
                if(wildcards.get(ary[1], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[1], 0) == 0):
                            wildcards[ary[1]] = [m]
                        else:
                            wildcards[ary[1]].append(m)
                if(wildcards.get(ary[2], 0) == 0):
                    for m in startState:
                        if(wildcards.get(ary[2], 0) == 0):
                            wildcards[ary[2]] = [m]
                        else:
                            wildcards[ary[2]].append(m)
                min_card = (None, None, 1000)
                for w in wildcards[ary[1]]:
                    for v in wildcards[ary[2]]:
                        if(v != w):
                            if(ary[3] == "on-top-of"):
                                dif = max([abs(w.x - v.x), abs(w.y - v.y), abs(w.z - 1 - v.z)])
                                if(v.top != w):
                                    temp_1 = copy.deepcopy(w)
                                    temp_2 = copy.deepcopy(v)
                                    while(temp_1.top != None):
                                        temp_1 = temp_1.top
                                        dif = dif + 1
                                        if(temp_1 != g[1]):
                                            dif = dif + 1
                                    while(temp_2.top != None):
                                        temp_2 = temp_2.top
                                        dif = dif + 1
                                        if(temp_2 != g[1]):
                                            dif = dif + 1
                                blocker = v.top
                                if(blocker != w and g[1] != w and blocker != None):
                                    dif = dif + 1
                                    
                            else:
                                dif1 = max([abs(w.x + 1 - v.x), abs(w.y - v.y), abs(w.z - v.z)])
                                dif2 = max([abs(w.x - 1 - v.x), abs(w.y - v.y), abs(w.z - v.z)])
                                dif3 = max([abs(w.x - v.x), abs(w.y + 1 - v.y), abs(w.z - v.z)])
                                dif4 = max([abs(w.x - v.x), abs(w.y - 1 - v.y), abs(w.z - v.z)])
                                dif = min([dif1, dif2, dif3, dif4])
                                if(w.z != v.z):
                                    temp_1 = copy.deepcopy(w)
                                    temp_2 = copy.deepcopy(v)
                                    while(temp_1.top != None and temp_2.top != None):
                                        temp_1 = temp_1.top
                                        temp_2 = temp_2.top
                                        dif = dif + 1
                                        if(temp_2 != g[1] or temp_1 != g[1]):
                                            dif = dif + 1
                            if(min_card[2] > dif):
                                min_card = (w, v, dif)
#                 blocks.append((min_card[1], ary[2]))
#                 blocks.append((min_card[0], ary[1]))
                dont.append(min_card[0].block_id)
                dont.append(min_card[1].block_id)
                if(ary[3] == "side-by-side" and min_card[1] not in min_card[0].sides):
                    sides1.append(min_card[0].block_id)
                    sides1.append(min_card[1].block_id)
                    if(min_card[0].z != min_card[1].z and min_card[1].top != None):
                        action.append("move " + min_card[1].block_id + " remove-top")
                    if(min_card[0].z != min_card[1].z and min_card[0].top != None):
                        action.append("move " + min_card[0].block_id + " remove-top")
                    if(min_card[0].z != min_card[1].z and min_card[0].below != None and len(min_card[0].below.sides) == 0 and min_card[1].below != None and len(min_card[1].below.sides) == 0):
                        if(min_card[0].z > min_card[1].z):
                            action.append("move " + min_card[1].block_id + " find-stack")
                        else:
                            action.append("move " + min_card[0].block_id + " find-stack")                            
                    action.append(ary[0] + " " + min_card[0].block_id + " " + min_card[1].block_id + " side-by-side")
                    
                    
                if(ary[3] == "on-top-of" and min_card[1].top != min_card[0]):
                    dont.append(min_card[0].block_id)
                    dont.append(min_card[1].block_id)
                    top1.append(min_card[0].block_id)
                    bottom1.append(min_card[1].block_id)
                    if(min_card[1].top != None):
                        action.append("move " + min_card[1].block_id + " remove-top")
                    if(min_card[0].top != None):
                        action.append("move " + min_card[0].block_id + " remove-top")
                    action.append(ary[0] + " " + min_card[0].block_id + " " + min_card[1].block_id + " on-top-of")
        if(action != []):
            actions.append(colors + action)   
    top = []
    bottom = []
    
    
    
    for a in actions:
        for b in a:
            if('on-top-of' in b):
                ary = b.split()
                top.append(ary[1])
                bottom.append(ary[2])
                
    for a in actions:
        for b in a:
            if('side-by-side' in b):
                ary = b.split()
                if(ary[1] in top):
                    top.append(ary[2])
                elif(ary[2] in top):
                    top.append(ary[1])
    remove = []            
    for c in actions:
        for d in c:
            ary = d.split()
            if(ary[2] in top):
                remove.append(c)
                
    for r in remove:
        actions.remove(r)
        
    e2 = copy.deepcopy(actions)
    for inde, e in enumerate(actions):
        for indf, f in enumerate(e):
            if('move' in f):
                e2[inde][indf] = f + " " + str(dont)[1:-1].replace(',', '').replace("'", "") 
    actions = e2
                

            
    return (actions, dont)

[['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'move block2 remove-top', 'is wildcard1 wildcard2 on-top-of\n'], ['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'is wildcard3 wildcard1 on-top-of']]

In [96]:
from random import randint
def take_action_H(action, state, dont):
    newState = copy.deepcopy(state)
    moves = []
    remove = []
    tops = []
    belows = []
    bottoms = {}
    sides = []
    repeat = []
    cost = 0
    moves = [] 
    print("actions1")
    print(action)    
    for a in action:
        ary = a.split()
        if(len(ary) > 0):
            if(ary[3] == "side-by-side"):
                sides.append(ary[1])
                sides.append(ary[2])
            if(ary[3] == "on-top-of"):
                tops.append(ary[1])
                belows.append(ary[2])
                bottoms[ary[1]] = ary[2]
                
                
    blocks = tops + belows + sides   
    print("BEFORE STATE")
    print(newState)
    print("actions2")
    print(action)
    actions2 = None
    actions3 = None
    act1a = None
    act1b = None
    act2a = None
    act2b = None
    
    for b in action:
        if(b != [None]):
            print("this is B!!")
            print(b)
            ary = b.split()
            if(len(ary) > 0):
                if(ary[3] == "side-by-side"):
                    if(ary[1] in tops and ary[2] not in tops):
    #                     moves = find_stack(ary[1], blocks, newState)
                        moves.append(remove_from_top(ary[2], blocks, newState))        
                        wildcard1 = "wildcard" + str(randint(0, 99999))
                        moves.append(find_stack(ary[1], blocks, newState))
                        act1a = "is " + bottoms.get(ary[1], None) + " " + wildcard1 + " side-by-side"
                        act1b = "is " + ary[2] + " " + wildcard1 + " on-top-of"
#                         actions2a, cost2a, parentState2a = aStarSearchLow(newState, [act1b], actions_2, take_action_2, h_5, 1000)
                        actions2b, cost2b, parentState2b = aStarSearchLow(newState, [act1a, act1b], actions_2, take_action_2, h_5, 1000)
                        cost = cost + cost2b
                        newState = parentState2b
#                         moves.append(actions2a)
                        moves.append(actions2b)
                        tops.append(ary[2])
                    if(ary[2] in tops and ary[1] not in tops):
    #                     moves = find_stack(ary[2], blocks, newState)
                        moves.append(remove_from_top(ary[1], blocks, newState))
                        wildcard2 = "wildcard" + str(randint(0, 99999))
                        moves.append(find_stack(ary[2], blocks, newState))
                        act2a = "is " + bottoms.get(ary[2], None) + " " + wildcard2 + " side-by-side"
                        act2b = "is " + ary[1] + " " + wildcard2 + " on-top-of"
#                         actions2c, cost2c, parentState2c = aStarSearchLow(newState, [act2b], actions_2, take_action_2, h_5, 1000)
                        actions2d, cost2d, parentState2d = aStarSearchLow(newState, [act2a, act2b], actions_2, take_action_2, h_5, 1000)
                        cost = cost + cost2d
                        newState = parentState2b
#                         moves.append(actions2c)
                        moves.append(actions2d)
                        tops.append(ary[1])
                    
    if(act1a != None):
        action.append(act1a)
    if(act1b != None):
        action.append(act1b)
    if(act2a != None):
        action.append(act2a)
    if(act2b != None):
        action.append(act2b)
    print("AFTER STATE")
    print(newState) 
    print("action2.5")
    print(action)
    for x in action:
        if(x != [None]):
            ary = x.split()
            if(len(ary) > 0):
                if(ary[0] == "move"):
                    if(ary[2] == "remove-top"):
                        print("before")
                        print("THISHERE")
                        print(ary[1])
                        moves.append(remove_from_top(ary[1], ary[3::], newState))
                        print("after")
                        remove.append(x)
            if(len(ary) > 0):
                if(ary[0] == "move"):
                    if(ary[2] == "find-stack"):
                        print("before2")
                        moves.append(find_stack(ary[1], ary[3::], newState))
                        print("after2")
                        remove.append(x)
    for r in remove:
        action.remove(r)
    print("before3")
    print(action)
    print(newState)
    actions, cost, parentState = aStarSearchLow(newState, action, actions_2, take_action_2, h_5, 1000)
    print("after3")

    return (moves + actions), (cost + len(moves)), parentState

In [22]:
def find_stack(block_str, wildcards, state):
    block_one = find2(block_str, state)
    
    actions = []
    while(block_one.below != None and len(block_one.below.sides) == 0):
        temp = block_one
        while(temp.below != None and len(temp.below.sides) == 0):
            temp = temp.below
        if(temp.z == 0):
            best = (None, 1000, 0)
            for s in state:
                if(s.z == 0 and s.block_id not in wildcards):
                    t = copy.deepcopy(s)
                    while(t.top != None and t.top.block_id not in wildcards and t.top.z > block_one.z - 1):
                        t = t.top
                    if(t.top == None and t.z > best[2]):
                        best = (t, max([abs(block_one.z - t.z), abs(block_one.y - t.y)]), t.z)
                    if(t.top == None and t.z == best[2] and max([abs(block_one.z - t.z), abs(block_one.y - t.y)]) < best[1]):
                        best = (t, max([abs(block_one.z - t.z), abs(block_one.y - t.y)]), t.z)
            if(best[0] != None):
                answer = aStarSearchLow(state, ["is " + temp.block_id + " " + best[0].block_id + " side-by-side"], actions_2, take_action_2, h_5, 1000)
                state = answer[2]
                actions = actions + answer[0][1::]
                g = get_grabbed(state)
                if(g[1] != None):
                    release(g[1], state)
                    actions.append(("release", (g[0], g[1].block_id)))
        elif(temp.z != 0):
            best = (None, 1000)
            for s in state:
                if(s.top == None and s.block_id not in wildcards and s != block_one):
                    if(max([abs(block_one.z - s.z), abs(block_one.y - s.y), abs(block_one.z - s.z)]) < best[1]):
                        best = (s, max([abs(block_one.z - s.z), abs(block_one.y - s.y), abs(block_one.z - s.z)]))
            if(best[0] != None):
                answer = aStarSearchLow(state, ["is " + temp.block_id + " " + best[0].block_id + " side-by-side"], actions_2, take_action_2, h_5, 1000)
                state = answer[2]
                actions = actions + answer[0][1::] 
                g = get_grabbed(state)
                if(g[1] != None):
                    release(g[1], state)
                    actions.append(("release", (g[0], g[1].block_id)))
        block_one = find2(block_str, state)
    return actions

In [94]:
def remove_from_top(block_str, wildcards, state):
    block_one = find2(block_str, state)
    actions = []
    print("here1")
    print(state)
    print(block_one)
    while(block_one.top != None):
        block_one = find2(block_str, state)
        temp = block_one
        print(temp)
        while(temp.top != None):
            temp = temp.top
        print(temp)
        check1 = (find(temp.x + 1, temp.y + 1, temp.z, state), (temp.x + 1, temp.y + 1, temp.z))
        check2 = (find(temp.x - 1, temp.y - 1, temp.z, state), (temp.x - 1, temp.y - 1, temp.z))
        check3 = (find(temp.x + 1, temp.y - 1, temp.z, state), (temp.x + 1, temp.y - 1, temp.z))
        check4 = (find(temp.x - 1, temp.y + 1, temp.z, state), (temp.x - 1, temp.y + 1, temp.z))
        check5 = (find(temp.x + 1, temp.y, temp.z, state), (temp.x + 1, temp.y, temp.z))
        check6 = (find(temp.x, temp.y + 1, temp.z, state), (temp.x, temp.y + 1, temp.z))
        check7 = (find(temp.x - 1, temp.y, temp.z, state), (temp.x - 1, temp.y, temp.z))
        check8 = (find(temp.x, temp.y - 1, temp.z, state), (temp.x, temp.y - 1, temp.z))
        checks = [check1, check2, check3, check4, check5, check6, check7, check8]
        remove = []
        for c in checks:
            if(c[1][0] < 0 or c[1][1] < 0 ):
                  remove.append(c)
                  
        for r in remove:
            checks.remove(r)
        not_found = True
        place = None
        while(not_found):
            check_copy = copy.deepcopy(checks)
            for indc, c in enumerate(checks):
                if(c[0] != None and c[0].top == None and c[0].block_id not in wildcards):
                    place = copy.deepcopy((c[1][0], c[1][1], c[1][2] + 1))
                    not_found = False
                elif(c[0] != None and c[0].top == None):
                    if((c[1][0] - temp.x) > 1):
                        newX = c[1][0] + 1
                    elif((c[1][0] - temp.x) < 1):
                        newX = c[1][0] - 1
                    else:
                        newX = c[1][0]
                    if((c[1][1] - temp.y) > 1):
                        newY = c[1][1] + 1
                    elif((c[1][1] - temp.y) < 1):
                        newY = c[1][1] - 1
                    else:
                        newY = c[1][1]
                    newpos = (find(newX, newY, c[1][2] + 1, state), (newX, newY, c[1][2] + 1))
                    while(newpos[0] != None):
                        newpos = (newpos[0].top, (newpos[1][0], newpos[1][1], newpos[1][2] + 1))
                    check_copy[indc] = copy.deepcopy(newpos)
                elif(c[0] != None and c[0].top != None):
                    check_copy[indc] = copy.deepcopy((c[0].top, (c[1][0], c[1][1], c[1][2] + 1)))
                elif(c[0] == None and (c[1][2] == 0 or ((find(c[1][0], c[1][1], c[1][2] - 1, state) != None) and find(c[1][0], c[1][1], c[1][2] - 1, state).block_id not in wildcards))):
                    place = copy.deepcopy((c[1][0], c[1][1], c[1][2]))
                    not_found = False
                elif(c[0] == None and (c[1][2] == 0 or find(c[1][0], c[1][1], c[1][2] - 1, state) != None)):
                    if((c[1][0] - temp.x) > 1):
                        newX = c[1][0] + 1
                    elif((c[1][0] - temp.x) < 1):
                        newX = c[1][0] - 1
                    else:
                        newX = c[1][0]
                    if((c[1][1] - temp.y) > 1):
                        newY = c[1][1] + 1
                    elif((c[1][1] - temp.y) < 1):
                        newY = c[1][1] - 1
                    else:
                        newY = c[1][1]
                    check_copy[indc] = copy.deepcopy((find(newX, newY, c[1][2], state), (newX, newY, c[1][2])))                    
                elif(c[0] == None):
                    check_copy[indc] = copy.deepcopy((find(c[1][0], c[1][1], c[1][2] - 1, state), (c[1][0], c[1][1], c[1][2] - 1)))
            checks = copy.deepcopy(check_copy)
        g = get_grabbed(state)
        if(g[1] != None):
            while(g[1].z != 0 and g[1].below == None):
                print("this")
                print(g[1])
                print(g[1].below)
                carry(g[1], 0, 0, -1, state)
                actions.append(("carry", (None, g[1].block_id), (0,0, -1)))
            release(g[1], state)
            actions.append(("release", (g[0], g[1].block_id)))
        print("temp")
        print(temp)
        grab(temp, state)
        actions.append(("grab", (None, temp.block_id)))
        if (place[2] == temp.z):
            move = 0
        elif (place[2] > temp.z):
            move = 1
        elif (place[2] < temp.z):
            move = -1
        while(move == 1 and (place[2] - temp.z) > 1 ):
            carry(temp, 0, 0, move, state)
            actions.append(("carry", (None, temp.block_id), (0,0, move)))
        carry(temp, place[0] - temp.x, place[1] - temp.y, move, state)
        actions.append(("carry", (None, temp.block_id), (block_one.x - place[0], block_one.y - place[1], move)))
        while(temp.z != place[2]):
            carry(temp, 0, 0, move, state)
            actions.append(("carry", (None, temp.block_id), (0, 0, move)))

        release(temp, state)
        actions.append(("release", (None, temp.block_id)))
        print("here2")
        print(block_one)
        print(state)
        block_one = find2(block_str, state)
    return actions

In [ ]:
startState = read_startState("input2.txt")
goalState = read_goalState("output2.txt")
print(startState)
print(actions_H(startState, goalState))
print(take_actiostartState = read_startState("input2.txt")
goalState = read_goalState("output2.txt")
print(startState)n_H(actions_H(startState, goalState)[0], startState))

In [88]:
def aStarHigh(parentNode, goalState, actionsF, take_actionF, hF, fmax):
    if(check(parentNode.state, goalState)):
        return(parentNode.moves, parentNode.g, parentNode.state)
    actions, dont = actionsF(parentNode.state, goalState)
    print("these actions")
    print(actions)
    if not actions:
        return("no more moves", float("inf"), parentNode.state)
    children = []
    for action in actions:
        moves, cost, childState = take_actionF(parentNode.action + action if parentNode.action != None else action, parentNode.state, dont)
        h = hF(childState, goalState)
        g = parentNode.g + cost
        f = max(h+g, parentNode.f)
        childNode = Node2(state=childState, action = parentNode.action + action if parentNode.action != None else action, moves = moves, h=h, g=g, f=f)
        children.append(childNode)
    while True:
        minChild = min(children, key = lambda x: x.f)
        if minChild.f > fmax:
            return ("max steps exceded", minChild.f, parentNode.state)
        alternativef = minChild.f if len(children) > 1 else float('inf')
        result, minChild.f, parentState = aStarHigh(minChild, goalState, actionsF, take_actionF, hF, min(fmax,alternativef))
        if result is not "no more moves" and result is not "max steps exceded":   
            if(parentNode.moves != None):
                result = parentNode.moves + result
            return (result, minChild.f, parentState) 
        
def aStarSearchHigh(startState, goalState, actionsF, take_actionF, hF, fmax):
    answer = aStarHigh(Node2(state=startState, action=None, moves=None, f=0, g=0, h=0), goalState, actionsF, take_actionF, hF, fmax)
    if((answer[0] ==  "max steps exceded") or (answer[0] == "no more moves")):
        print(answer)
    else:
        for a in answer[0]:
            if(a != None):
                print("(" + str(a[0]) + ", " + str(a[1][1]) + ("" if (len(a) == 2) else (", " + str(a[2]))) + ")")
        print(answer[1])
        return answer[2]

In [ ]:
startState = read_startState("input2.txt")
goalState = read_goalState("output2.txt")
print(startState)
for s in startState:
    remove_from_top(s.block_id, [], startState)
state = aStarSearchHigh(startState, goalState, actions_H, take_action_H, h_5, 1000)

[{block1, (1, 1, 0), (color: red), (on-top-of: block2), (side-by-side: [])}
, {block2, (1, 1, 1), (color: blue), (on-top-of: block5), (side-by-side: [])}
, {block4, (3, 2, 0), (color: green), (on-top-of: None), (side-by-side: [])}
, {block5, (1, 1, 2), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: block8), (side-by-side: [])}
, {block8, (4, 4, 1), (color: purple), (on-top-of: None), (side-by-side: [])}
]
here1
[{block1, (1, 1, 0), (color: red), (on-top-of: block2), (side-by-side: [])}
, {block2, (1, 1, 1), (color: blue), (on-top-of: block5), (side-by-side: [])}
, {block4, (3, 2, 0), (color: green), (on-top-of: None), (side-by-side: [])}
, {block5, (1, 1, 2), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: block8), 

FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (2, 2, 0), (color: red), (on-top-of: None), (side-by-side: ['block4', 'block6'])}
, {block2, (1, 0, 1), (color: blue), (on-top-of: None), (side-by-side: [])}
, {block4, (3, 2, 0), (color: green), (on-top-of: None), (side-by-side: ['block1'])}
, {block5, (1, 0, 0), (color: purple), (on-top-of: block2), (side-by-side: [])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: ['block1'])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: None), (side-by-side: ['block8'])}
, {block8, (4, 3, 0), (color: purple), (on-top-of: None), (side-by-side: ['block7'])}
]
goal
['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'has wildcard4 color purple\n', 'has wildcard5 color purple\n', 'is block4 block1 on-top-of']
heuristic
Start
FINISH
1
childaction
('carry', (0, 'block1'), (1, 1, 0))
allactions
[('release', (0,

Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (1, 1, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5'])}
, {block2, (0, 0, 0), (color: blue), (on-top-of: None), (side-by-side: ['block5'])}
, {block4, (1, 1, 1), (color: green), (on-top-of: None), (side-by-side: [])}
, {block5, (1, 0, 0), (color: purple), (on-top-of: None), (side-by-side: ['block1', 'block2'])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: None), (side-by-side: ['block8'])}
, {block8, (4, 3, 0), (color: purple), (on-top-of: None), (side-by-side: ['block7'])}
]
goal
['is block1 wildcard70427 side-by-side', 'is block5 wildcard70427 on-top-of']
heuristic
Start
FINISH
1
childaction
('releas

FINISH
child
[{block1, (1, 1, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5', 'block2'])}
, {block2, (0, 1, 0), (color: blue), (on-top-of: None), (side-by-side: ['block1'])}
, {block4, (1, 1, 1), (color: green), (on-top-of: None), (side-by-side: [])}
, {block5, (1, 0, 0), (color: purple), (on-top-of: None), (side-by-side: ['block1'])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: None), (side-by-side: ['block8'])}
, {block8, (4, 3, 0), (color: purple), (on-top-of: None), (side-by-side: ['block7'])}
]
goal
['is block1 wildcard70427 side-by-side', 'is block5 wildcard70427 on-top-of']
heuristic
Start
FINISH
1
childaction
('grab', (1, 'block2'))
allactions
[('grab', (1, 'block2')), ('grab', (2, 'block4')), ('grab', (3, 'block5')), ('grab', (4, 'block6')), ('grab', (5, 'block7')), ('grab', (6, 'block8')), ('slide', (0, 'block1'), (-1, 1)), ('slide', (0, 'block1'), (0, 1)), ('slide', (0, 'bloc

goalState
['is block1 wildcard70427 side-by-side', 'is block5 wildcard70427 on-top-of']
Wildcard not initialized2
{'wildcard70427': [{block5, (1, 0, 0), (color: purple), (on-top-of: None), (side-by-side: ['block1', 'block2'])}
]}
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (1, 1, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5'])}
, {block2, (0, 0, 0), (color: blue), (on-top-of: None), (side-by-side: ['block5'])}
, {block4, (1, 1, 1), (color: green), (on-top-of: None), (side-by-side: [])}

...

Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (0, 0, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5'])}
, {block2, (1, 0, 1), (color: blue), (on-top-of: None), (side-by-side: ['block4'])}
, {block4, (0, 0, 1), (color: green), (on-top-of: None), (side-by-side: ['block2'])}
, {block5, (1, 0, 0), (color: purple), (on-top-of: block2), (side-by-side: ['block1'])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (5, 5, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block8, (4, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
]
goal
['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'has wildcard4 color purple\n', 'has wildcard5 color purple\n', 'is block4 block1 on-top-of', 'has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'has wildcard4 color purple\n', 'has wildcard5 color purple\n', 'is block4 block5 sid

FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (0, 0, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5'])}
, {block2, (1, 0, 1), (color: blue), (on-top-of: None), (side-by-side: ['block4'])}
, {block4, (0, 0, 1), (color: green), (on-top-of: None), (side-by-side: ['block2'])}
, {block5, (1, 0, 0), (color: purple), (on-top-of: block2), (side-by-side: ['block1'])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block8, (5, 2, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
]
goal
['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'h

allactions
[('grab', (1, 'block2')), ('grab', (2, 'block4')), ('grab', (4, 'block6')), ('grab', (5, 'block7')), ('grab', (6, 'block8')), ('slide', (0, 'block1'), (0, 1)), ('slide', (0, 'block1'), (1, 1)), ('slide', (0, 'block1'), (1, 0)), ('slide', (0, 'block1'), (1, -1)), ('slide', (3, 'block5'), (1, 1)), ('slide', (3, 'block5'), (1, 0)), ('slide', (3, 'block5'), (1, -1)), ('slide', (3, 'block5'), (0, -1)), ('slide', (4, 'block6'), (-1, 1)), ('slide', (4, 'block6'), (0, 1)), ('slide', (4, 'block6'), (1, 1)), ('slide', (4, 'block6'), (1, 0)), ('slide', (4, 'block6'), (1, -1)), ('slide', (4, 'block6'), (0, -1)), ('slide', (4, 'block6'), (-1, -1)), ('slide', (4, 'block6'), (-1, 0)), ('slide', (5, 'block7'), (-1, 1)), ('slide', (5, 'block7'), (0, 1)), ('slide', (5, 'block7'), (1, 1)), ('slide', (5, 'block7'), (1, 0)), ('slide', (5, 'block7'), (1, -1)), ('slide', (5, 'block7'), (-1, -1)), ('slide', (5, 'block7'), (-1, 0)), ('slide', (6, 'block8'), (-1, 1)), ('slide', (6, 'block8'), (1, 1))

heuristic
Start
FINISH
3
childaction
('slide', (4, 'block6'), (-1, 0))
allactions
[('grab', (1, 'block2')), ('grab', (2, 'block4')), ('grab', (4, 'block6')), ('grab', (5, 'block7')), ('grab', (6, 'block8')), ('slide', (0, 'block1'), (-1, 1)), ('slide', (0, 'block1'), (0, 1)), ('slide', (0, 'block1'), (1, 1)), ('slide', (0, 'block1'), (1, 0)), ('slide', (0, 'block1'), (1, -1)), ('slide', (0, 'block1'), (0, -1)), ('slide', (0, 'block1'), (-1, -1)), ('slide', (3, 'block5'), (0, 1)), ('slide', (3, 'block5'), (1, 1)), ('slide', (3, 'block5'), (1, -1)), ('slide', (3, 'block5'), (0, -1)), ('slide', (4, 'block6'), (-1, 1)), ('slide', (4, 'block6'), (0, 1)), ('slide', (4, 'block6'), (1, 1)), ('slide', (4, 'block6'), (1, 0)), ('slide', (4, 'block6'), (1, -1)), ('slide', (4, 'block6'), (0, -1)), ('slide', (4, 'block6'), (-1, -1)), ('slide', (4, 'block6'), (-1, 0)), ('slide', (5, 'block7'), (-1, 1)), ('slide', (5, 'block7'), (0, 1)), ('slide', (5, 'block7'), (1, 1)), ('slide', (5, 'block7'), (1, 0

FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
Start
FINISH
child
[{block1, (1, 1, 0), (color: red), (on-top-of: block4), (side-by-side: ['block5'])}
, {block2, (0, 1, 1), (color: blue), (on-top-of: None), (side-by-side: ['block4'])}
, {block4, (1, 1, 1), (color: green), (on-top-of: None), (side-by-side: ['block2'])}
, {block5, (0, 1, 0), (color: purple), (on-top-of: block2), (side-by-side: ['block1'])}
, {block6, (2, 3, 0), (color: purple), (on-top-of: None), (side-by-side: [])}
, {block7, (4, 4, 0), (color: purple), (on-top-of: None), (side-by-side: ['block8'])}
, {block8, (3, 4, 0), (color: purple), (on-top-of: None), (side-by-side: ['block7'])}
]
goal
['has wildcard1 color red\n', 'has wildcard2 color blue\n', 'has wildcard3 color green\n', 'has wildcard4 color purple\n', 'has w

In [ ]:
check(state, goalState)